### An engineering problem from "Engineering Optimization" by Xin-She Yang

Goal: Design an optimal spring (cheapest / least material needed) that does the job. Parameters we can change: $d$, the diameter of the coil; $L$, the length of the spring; $w$, the thickness of the wire.

Task: Minimize $$(2+L)dw^2$$ subject to the constraints
\begin{align*}
g_1(L,d,w) &= 1 - \frac{d^3L}{7178w^4} \leq 0\\[5pt]
g_2(L,d,w) &= \frac{4d^2 - wd}{12566dw^3 - w^4} + \frac{1}{5108w^2} - 1 \leq 0\\[5pt]
g_3(L,d,w) &= 1 - \frac{140.45w}{d^2L} \leq 0\\[5pt]
g_4(L,d,w) &= \frac{w+d}{1.5} - 1 \leq 0
\end{align*}
with boundary conditions
$$
0.05 \leq w \leq 2.0
\qquad\qquad
0.25 \leq d \leq 1.3
\qquad\qquad
2.0 \leq L \leq 15.0
$$

In [1]:
import math
import random

In [4]:
def random_in_range(lower, upper):
    return random.random() * (upper - lower) + lower
random_in_range(2, 15)

2.0116314006633185

In [6]:
def g1(L,d,w):
    return 1 - d**3 * L / (7178 * w**4)

def g2(L,d,w):
    return (4*d**2 - w*d)/(12566 * d * w**3 - w**4) + 1/(5108*w**2) - 1

def g3(L,d,w):
    return 1 - 140.45 * w / (d**2*L)

def g4(L,d,w):
    return (w+d)/1.5 - 1

def satisfies_constraints(L,d,w):
    return g1(L,d,w) <= 0 and g2(L,d,w) <= 0 and g3(L,d,w) <= 0 and g4(L,d,w) <= 0

In [7]:
satisfies_constraints(*[14.58629717, 0.07341016, 0.0299435 ])

False

In [10]:
L, d, w = [14.68629717, 0.07341016, 0.0299435]
g1(L,d,w), g2(L,d,w), g3(L,d,w), g4(L,d,w)

(-0.006855439166644661,
 -2.3389332648449113e-07,
 -52.13732073627852,
 -0.93109756)

In [11]:
def score(L,d,w):  # w-squared is "w**2" not "w^2"
    return (2+L)*d*w**2

In [64]:
def tweak(L,d,w):
    # new_w = old_w + a number between -delta_w and +delta_w

    delta_w = 0.01
    delta_d = 0.01
    delta_L = 0.1
    
    new_w = w + random_in_range(-1, 1) * delta_w
    while new_w < 0.05 or new_w > 2:
        new_w = w + random_in_range(-1, 1) * delta_w
    
    new_d = d + random_in_range(-1, 1) * delta_d
    while new_d < 0.25 or new_d > 1.3:
        new_d = d + random_in_range(-1, 1) * delta_d
        
    new_L = L + random_in_range(-1, 1) * delta_L
    while new_L < 2 or new_L > 15:
        new_L = L + random_in_range(-1, 1) * delta_L
        
    return (new_L, new_d, new_w)
        
tweak(15, 1.3, 2.0)

(14.990587393577437, 1.290393908302358, 1.990592195970753)

In [65]:
def random_solution():
    return (
        random_in_range(2, 15),
        random_in_range(0.25, 1.3),
        random_in_range(0.05, 2),
    )
print(random_solution())

(6.173509817073723, 0.6703061072447234, 1.8972620984245134)


In [66]:
# what does the * do
def test(num1, num2):
    return num1 + num2
L = [1,3]
test(*L)

4

In [67]:
def hill_climbing():
    
    start = random_solution()
    while not satisfies_constraints(*start):
        # print("fail ", end="")
        start = random_solution()
    sol = start
    value = score(*sol)
    # print(sol, value)

    bad = 0
    while True:
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            # print("fail ", end="")
            new_sol = tweak(*sol)
        new_value = score(*new_sol)
        if new_value < value:
            bad = 0
            sol = new_sol
            value = new_value
            # print(sol, value)
            
        else:
            bad += 1
            if bad > 1000:
                # print(value)
                return sol
    


In [68]:
sol = hill_climbing()
print(sol)

# print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))
print(score(*sol))

(2.0081370046195417, 0.28215836682942713, 0.05004142068745657)
0.0028320098057205713


In [72]:
# smarter: sample 1000 tweaks to find a good initial_temp that gives a desired p_0
# or: heat the system slowly until the % of worsening solutions is what you want
initial_temp = 0.005
alpha = 0.99
final_temp = initial_temp / 10000
trials_per_temp = 10000

start = random_solution()
while not satisfies_constraints(*start):
    start = random_solution()
sol = start
value = score(*sol)

In [73]:
temp = initial_temp
generation = 0
best_sol = None
best_score = None

while temp >= final_temp:
    generation += 1
    accepted_worse = 0
    total_worse = 0
    for i in range(trials_per_temp):
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            new_sol = tweak(*sol)

        new_value = score(*new_sol)
        
        delta = new_value - value
        delta *= -1
        if delta >= 0:
            sol = new_sol
            value = new_value
            if best_score is None or value < best_score:
                best_sol = sol
                best_score = value
        else:
            total_worse += 1
            p = math.exp(delta/temp)
            r = random.random()
            if r <= p:
                accepted_worse += 1
                sol = new_sol
                value = new_value

    print(
        f"Gen #{generation}: temp = {temp:.6f}, "
        f"best score = {best_score:.8f}, "
        f"cur score = {value:.8f}, "
        f"worse accepted = {round(accepted_worse/total_worse*100,2):.2f}%"
    )
    temp = temp * alpha
    


Gen #1: temp = 0.005000, best score = 0.00327325, cur score = 0.00496140, worse accepted = 63.28%
Gen #2: temp = 0.004950, best score = 0.00327325, cur score = 0.00788659, worse accepted = 65.36%
Gen #3: temp = 0.004901, best score = 0.00295824, cur score = 0.01637738, worse accepted = 73.90%
Gen #4: temp = 0.004851, best score = 0.00295824, cur score = 0.02437785, worse accepted = 70.61%
Gen #5: temp = 0.004803, best score = 0.00295824, cur score = 0.01333553, worse accepted = 70.37%
Gen #6: temp = 0.004755, best score = 0.00295824, cur score = 0.01078134, worse accepted = 73.38%
Gen #7: temp = 0.004707, best score = 0.00295824, cur score = 0.01590679, worse accepted = 69.59%
Gen #8: temp = 0.004660, best score = 0.00295824, cur score = 0.00715232, worse accepted = 73.66%
Gen #9: temp = 0.004614, best score = 0.00295824, cur score = 0.00673628, worse accepted = 71.59%
Gen #10: temp = 0.004568, best score = 0.00295824, cur score = 0.00682861, worse accepted = 72.24%
Gen #11: temp = 0.0

In [71]:
best_sol


(2.0020773811812647, 0.2819354884901672, 0.050000764463366584)

In [75]:
score(2.0020773811812647, 0.2819354884901672, 0.050000764463366584)

0.00282090536077111

In [76]:
best_sol
score(*best_sol)

0.0028210512997475156

In [ ]:
sol = best_sol
print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))

In [ ]:
score(*sol)